In [ ]:
import sys
print(sys.version)
import numpy as np
import matplotlib.pyplot as plt
import plotly as plotly
import plotly.graph_objects as go
from mined_metric.jupyter.utils.data_access_util import get_experiment_data, chum_summary_stats
from mined_metric.jupyter.utils.prediction_util import collect_errors, collect_samples, calculate_hist

In [ ]:
EXPERIMENT_IDS = ["EXPERIMENT_ID_PLACEHOLDER"]

exp_datas = {}

for experiment_id in EXPERIMENT_IDS:
    exp_data = get_experiment_data(experiment_id)
    if "exception" in exp_data:
        print("Invalid data is returned: %s" % exp_data["exception"])
    exp_datas[experiment_id] = exp_data

all_samples = collect_samples(exp_datas)

In [ ]:
percentiles = [0.5, 0.75, 0.9]
tags = ['l2', 'matched_l2', 'matched_s', 'matched_t', 'most_likely_l2', 'most_likely_s', 'most_likely_t', 'min_track_l2', 'min_track_s', 'min_track_t', 's', 't']
for tag in tags:
    print('Tag: %s' % tag)
    fig = go.Figure()
    fig.update_layout(
        autosize=False,
        width=800,
        height=600,
    )
    fig.update_layout(
        title='Percentile Errors vs Time',
        xaxis_title='Time (seconds)',
        yaxis_title='Error (m)'
    )
    for experiment_id, samples in all_samples.items():
        samples_with_tag = []
        for sample in samples:
            if tag in sample['tags']:
                samples_with_tag.append(sample)
        total_samples = len(samples_with_tag)
        timesteps = samples_with_tag[0]['time_series_regression_result']['time']
        print('Number of samples in experiemnt {}: {}'.format(experiment_id, total_samples))

        error_vec_timesteps = []
        for index, timestep in enumerate(timesteps):
            errors = collect_errors(samples_with_tag, index)
            error_vec_timesteps.append(errors)
        
        metrics = []
        dtype = [('timestamp', float), ('error', float)]
        for percentile in percentiles:
            metric = []
            for index, timestep in enumerate(timesteps):
                errors = error_vec_timesteps[index]
                offset = min(int(percentile * len(errors)), len(errors) - 1)
                value = errors[offset]
                metric.append(value)
            points = np.empty(len(timesteps), dtype=dtype)
            for i in range(len(timesteps)):
                points[i] = (timesteps[i], metric[i])
            fig = fig.add_trace(go.Scatter(
                name='{}-p{}'.format(experiment_id, int(100 * percentile)),
                x=points['timestamp'], 
                y=points['error'])) 

fig.show()

In [ ]:
fig = go.Figure()
fig.update_layout(
    autosize=False,
    width=800,
    height=600,
)
fig.update_layout(
    title='Percentile Errors vs Time',
    xaxis_title='Time (seconds)',
    yaxis_title='Error (m)'
)

for experiment_id, samples in all_samples.items():
    sum_weights = []
    samples_with_tag = []
    for sample in samples:
        if 'sum_weight_matched_rfts' in sample['tags']:
            samples_with_tag.append(sample)
            sum_weights.append(sample['regression_result']['error'])
    total_samples = len(samples_with_tag)
    print('Number of samples: %d' % total_samples)

    sum_weights = sorted(sum_weights)

    bins = []
    for i in range(-1, 101):
        bins.append(i / 10.0)

    hist = calculate_hist(bins, sum_weights)

    print('Tag: sum_weight_matched_rfts')

    dtype = [('x', float), ('y', float)]
    points = np.empty(len(hist), dtype=dtype)
    for i in range(len(hist)):
        points[i] = (bins[i + 1], hist[i])
    fig = fig.add_trace(go.Scatter(
        name=experiment_id,
        x=points['x'], 
        y=points['y']
    ))
    
fig.show()